In [1]:
#!pip install selenium
#!pip install webdriver-manager
#스레드: 여러 작업을 동시에 하기 위함 = 같은 작업을 빠르게 하기 위함
#크리티컬섹션: 공유되고 있는 값

In [2]:
from flask import Flask, url_for, request, jsonify, redirect, Response
from flask_cors import CORS, cross_origin

import json
import requests

import selenium
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager

import threading
import time
import logging

import pickle

In [3]:
CRAWLED_RES_SAVED_FILE = 'crawl_data/result'

In [4]:
# 기록용 스레드
def record_thread(cond):
    print("기록용 스레드 구동 시작!")
    cnt = 0
    
    while True:
        if crawl_fin:
            f = open(CRAWLED_RES_SAVED_FILE, 'wb')
            pickle.dump(hrefURL, f)
            f.close()
            
        time.sleep(1)

In [5]:
# 관리 스레드
# 크롤링이 끝나면 다시 크롤링을 시작함
def thread_manager(cond):
    print("스레드 매니저 구동 시작")
    
    while True:
        with cond:
            if crawl_fin:
                cond.notifyAll()
                
            time.sleep(1)

In [6]:
# 크롤링 스레드
def crawl_thread(cond, text):
    global crawl_fin
    crawl_fin = False
    
    print("크롤링 스레드 구동 시작!")
    
    url = "https://www.youtube.com/results?search_query="
    
    #https://chromedriver.chromium.org/downloads 에서 버전에 맞게 다운로드
    #chrome_driver 위치에서 %xattr -d com.apple.quarantine chromedriver
    driver = webdriver.Chrome("/Users/ljieun/Desktop/chrome_driver/chromedriver")
    
    search_url = url + text
    
    driver.get(url = search_url)
    
    while True:
        with cond:
            body = driver.find_element(By.TAG_NAME, 'body')
            
            global hrefURL
            hrefURL = set()
            
            shelfContents = driver.find_elements(
                By.CSS_SELECTOR,
                "#contents > ytd-shelf-renderer > div > div > ytd-vertical-list-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
            )
            
            for item in shelfContents:
                if (item != ''):
                    hrefURL.add(item.get_attribute('href'))
                    
            backup_height = driver.execute_script("return document.body.scrollHeight")
                    
            while True:
                body.send_keys(Keys.END)
                time.sleep(2)
                
                current_height = driver.execute_script("return document.body.scrollHeight")
                
                if backup_height == current_height:
                    break
                    
                backup_height = current_height
                    
            allContents = driver.find_elements(
                By.CSS_SELECTOR,
                "#contents > ytd-item-section-renderer > div > ytd-video-renderer > div > ytd-thumbnail > a"
            )
            
            for item in allContents:
                if (item != ''):
                    hrefURL.add(item.get_attribute('href'))
            
            print(hrefURL)
            print(len(hrefURL))
            
            crawl_fin = True
            cond.wait()
            crawl_fin = False


In [ ]:
if __name__ == '__main__':
    cond = threading.Condition()
    crawler = threading.Thread(name = 'Crawler', target = crawl_thread, args = (cond, '시고르자브종'))
    recorder = threading.Thread(name = 'Recorder', target = record_thread, args = (cond, ))
    manager = threading.Thread(name = 'Manager', target = thread_manager, args = (cond, ))
    
    crawler.start()
    time.sleep(2)
    recorder.start()
    manager.start()
    
    crawler.join()
    recorder.join()
    manager.join()

크롤링 스레드 구동 시작!


/var/folders/bs/7lq97vjs07l7dkfh431gjctc0000gn/T/ipykernel_12186/619981653.py:12: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome("/Users/ljieun/Desktop/chrome_driver/chromedriver")


기록용 스레드 구동 시작!
스레드 매니저 구동 시작


/var/folders/bs/7lq97vjs07l7dkfh431gjctc0000gn/T/ipykernel_12186/619981653.py:25: DeprecationWarning: find_elements_by_css_selector is deprecated. Please use find_elements(by=By.CSS_SELECTOR, value=css_selector) instead
  shelfContents = driver.find_elements_by_css_selector(


{'https://www.youtube.com/shorts/8CiT81i29uU', 'https://www.youtube.com/watch?v=kt79xmVNF5A', 'https://www.youtube.com/shorts/yu9--BCqPr4', 'https://www.youtube.com/watch?v=FR1uIeQcj1Q', 'https://www.youtube.com/watch?v=U3StPYZ_cpM', 'https://www.youtube.com/watch?v=Kz9njANzMQA', 'https://www.youtube.com/watch?v=42fvJ5skggc', 'https://www.youtube.com/watch?v=wgPowY0G4Sw', 'https://www.youtube.com/watch?v=JLkAv6kwGJw', 'https://www.youtube.com/shorts/spc69-pCbbw', 'https://www.youtube.com/shorts/22_1CRL35Qk', 'https://www.youtube.com/watch?v=ePSG2dJvx48', 'https://www.youtube.com/watch?v=nfbGqacJtmw', 'https://www.youtube.com/watch?v=CxO_kiCpzQI', 'https://www.youtube.com/shorts/hGPOoeOF3j8', 'https://www.youtube.com/watch?v=mA1sz4nbIV8', 'https://www.youtube.com/shorts/KHkZivSQdSk', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=-XYSZpWvSGs', 'https://www.youtube.com/watch?v=HwIEerKNZqw', 'https://www.youtube.com/watch?v=nlnAzzb192g', 'https://www.youtub

...

{'https://www.youtube.com/watch?v=IpaKN7F6M4U', 'https://www.youtube.com/watch?v=p29MH-chEbw', 'https://www.youtube.com/watch?v=WGk0t-yj2vM', 'https://www.youtube.com/watch?v=FG4E9lHxEiQ', 'https://www.youtube.com/watch?v=wd1GTiq2K1g', 'https://www.youtube.com/watch?v=2jwOJAAJ-ao', 'https://www.youtube.com/shorts/czrqYhk757M', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=L9dEwQ7t5Mk', 'https://www.youtube.com/watch?v=MF8gyzm9R1U', 'https://www.youtube.com/watch?v=3HuraViwbRQ', 'https://www.youtube.com/watch?v=izsvmRLHHRk', 'https://www.youtube.com/watch?v=XHdY6Sb3wi0', 'https://www.youtube.com/watch?v=yZ9n7jWLzFU', 'https://www.youtube.com/shorts/8fZSqS-fS2M', 'https://www.youtube.com/watch?v=KeYyT2_U4UY', 'https://www.youtube.com/watch?v=_eDVD-LzaT4', 'https://www.youtube.com/watch?v=Yg4m65Yu7tM', 'https://www.youtube.com/watch?v=xQ0-vrmwAf8', 'https://www.youtube.com/shorts/HwxLu34V_0k', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.you

{'https://www.youtube.com/watch?v=IpaKN7F6M4U', 'https://www.youtube.com/watch?v=p29MH-chEbw', 'https://www.youtube.com/watch?v=WGk0t-yj2vM', 'https://www.youtube.com/watch?v=FG4E9lHxEiQ', 'https://www.youtube.com/watch?v=wd1GTiq2K1g', 'https://www.youtube.com/watch?v=2jwOJAAJ-ao', 'https://www.youtube.com/shorts/czrqYhk757M', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=L9dEwQ7t5Mk', 'https://www.youtube.com/watch?v=MF8gyzm9R1U', 'https://www.youtube.com/watch?v=3HuraViwbRQ', 'https://www.youtube.com/watch?v=izsvmRLHHRk', 'https://www.youtube.com/watch?v=XHdY6Sb3wi0', 'https://www.youtube.com/watch?v=yZ9n7jWLzFU', 'https://www.youtube.com/shorts/8fZSqS-fS2M', 'https://www.youtube.com/watch?v=KeYyT2_U4UY', 'https://www.youtube.com/watch?v=_eDVD-LzaT4', 'https://www.youtube.com/watch?v=Yg4m65Yu7tM', 'https://www.youtube.com/watch?v=xQ0-vrmwAf8', 'https://www.youtube.com/shorts/HwxLu34V_0k', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.you

{'https://www.youtube.com/watch?v=IpaKN7F6M4U', 'https://www.youtube.com/watch?v=p29MH-chEbw', 'https://www.youtube.com/watch?v=WGk0t-yj2vM', 'https://www.youtube.com/watch?v=FG4E9lHxEiQ', 'https://www.youtube.com/watch?v=wd1GTiq2K1g', 'https://www.youtube.com/watch?v=2jwOJAAJ-ao', 'https://www.youtube.com/shorts/czrqYhk757M', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=L9dEwQ7t5Mk', 'https://www.youtube.com/watch?v=MF8gyzm9R1U', 'https://www.youtube.com/watch?v=3HuraViwbRQ', 'https://www.youtube.com/watch?v=izsvmRLHHRk', 'https://www.youtube.com/watch?v=XHdY6Sb3wi0', 'https://www.youtube.com/watch?v=yZ9n7jWLzFU', 'https://www.youtube.com/shorts/8fZSqS-fS2M', 'https://www.youtube.com/watch?v=KeYyT2_U4UY', 'https://www.youtube.com/watch?v=_eDVD-LzaT4', 'https://www.youtube.com/watch?v=Yg4m65Yu7tM', 'https://www.youtube.com/watch?v=xQ0-vrmwAf8', 'https://www.youtube.com/shorts/HwxLu34V_0k', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.you

{'https://www.youtube.com/watch?v=IpaKN7F6M4U', 'https://www.youtube.com/watch?v=p29MH-chEbw', 'https://www.youtube.com/watch?v=WGk0t-yj2vM', 'https://www.youtube.com/watch?v=FG4E9lHxEiQ', 'https://www.youtube.com/watch?v=wd1GTiq2K1g', 'https://www.youtube.com/watch?v=2jwOJAAJ-ao', 'https://www.youtube.com/shorts/czrqYhk757M', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=L9dEwQ7t5Mk', 'https://www.youtube.com/watch?v=MF8gyzm9R1U', 'https://www.youtube.com/watch?v=3HuraViwbRQ', 'https://www.youtube.com/watch?v=izsvmRLHHRk', 'https://www.youtube.com/watch?v=XHdY6Sb3wi0', 'https://www.youtube.com/watch?v=yZ9n7jWLzFU', 'https://www.youtube.com/shorts/8fZSqS-fS2M', 'https://www.youtube.com/watch?v=KeYyT2_U4UY', 'https://www.youtube.com/watch?v=_eDVD-LzaT4', 'https://www.youtube.com/watch?v=Yg4m65Yu7tM', 'https://www.youtube.com/watch?v=xQ0-vrmwAf8', 'https://www.youtube.com/shorts/HwxLu34V_0k', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.you

{'https://www.youtube.com/watch?v=IpaKN7F6M4U', 'https://www.youtube.com/watch?v=p29MH-chEbw', 'https://www.youtube.com/watch?v=WGk0t-yj2vM', 'https://www.youtube.com/watch?v=FG4E9lHxEiQ', 'https://www.youtube.com/watch?v=wd1GTiq2K1g', 'https://www.youtube.com/watch?v=2jwOJAAJ-ao', 'https://www.youtube.com/shorts/czrqYhk757M', 'https://www.youtube.com/shorts/dxQSq-hhbbI', 'https://www.youtube.com/watch?v=L9dEwQ7t5Mk', 'https://www.youtube.com/watch?v=MF8gyzm9R1U', 'https://www.youtube.com/watch?v=3HuraViwbRQ', 'https://www.youtube.com/watch?v=izsvmRLHHRk', 'https://www.youtube.com/watch?v=XHdY6Sb3wi0', 'https://www.youtube.com/watch?v=yZ9n7jWLzFU', 'https://www.youtube.com/shorts/8fZSqS-fS2M', 'https://www.youtube.com/watch?v=KeYyT2_U4UY', 'https://www.youtube.com/watch?v=_eDVD-LzaT4', 'https://www.youtube.com/watch?v=Yg4m65Yu7tM', 'https://www.youtube.com/watch?v=xQ0-vrmwAf8', 'https://www.youtube.com/shorts/HwxLu34V_0k', 'https://www.youtube.com/watch?v=7AM9TrlWcDM', 'https://www.you

In [ ]:
#크롤링 첫결과 669개

#Mac core 개수확인
#system_profiler|grep Cores
#system_profiler|grep processors
#syscil hw.ncpu

In [ ]:
# import pickle

# f = open(CRAWLED_RES_SAVED_FILE, 'rb')
# hrefURL = pickle.load(f)
# f.close()

# print(hrefURL)